# Assignment 1
You should submit the **UniversityNumber.ipynb** file and your final prediction file **UniversityNumber.test.out** to Moodle. Make sure your code does not use your local files and that the results are reproducible. Before submitting, please **run your notebook and keep all running logs** so that we can check.

## 1 $n$-gram Language Model
**Q1**: Expand the above definition of $ p(\vec{w})$ using naive estimates of the parameters, such as $  p(w_4 \mid w_2, w_3) \stackrel{\tiny{\mbox{def}}}{=}  \frac{C(w_2~w_3~w_4)}{C(w_2~w_3)} $ where \( C(w_2 w_3 w_4) \) denotes the count of times the trigram $ w_2 w_3 w_4 $ was observed in a training corpus.

**Write your answer:**
$ p(w) {=} \frac{C(w_1)}{V}  \frac{C(w_1~w_2)}{C(w_1)} \frac{C(w_1~w_2~w_3)}{C(w_1~w_2)} \frac{C(w_2~w_3~w_4)}{C(w_2~w_3)} \frac{C(w_{n-2}~w_{n-1}~w_n)}{C(w_{n-2}~w_{n-1})} \\ {=} \frac{C(w_1~w_2~w_3)}{V} \frac{C(w_2~w_3~w_4)}{C(w_2~w_3)} \frac{C(w_{n-2}~w_{n-1}~w_n)}{C(w_{n-2}~w_{n-1})} $ 



**Q2**: One could also define a kind of reversed trigram language model $p_{reversed}$ that instead assumed the words were generated in reverse order (from right to left):
\begin{align} p_{reversed}(\vec{w}) \stackrel{\tiny{\mbox{def}}}{=}&p(w_n) \cdot p(w_{n-1} \mid w_n) \cdot p(w_{n-2} \mid w_{n-1} w_n) \cdot p(w_{n-3} \mid w_{n-2} w_{n-1}) \\ &\cdots p(w_2 \mid w_3 w_4) \cdot p(w_1 \mid w_2 w_3) \end{align}
By manipulating the notation, show that the two models are identical, i.e., $ p(\vec{w}) = p_{reversed}(\vec{w}) $ for any $ \vec{w} $ provided that both models use MLE parameters estimated from the same training data (see Q1 above).

**Write your answer:**
$ p_{reserved}(w) {=} \frac{C(w_n)}{V}  \frac{C(w_{n-1}~w_{n})}{C(w_{n})} \frac{C(w_{n-2}~w_{n-1}~w_n)}{C(w_{n-1}~w_{n})} \frac{C(w_{n-3}~w_{n-2}~w_{n-1})}{C(w_{n-2}~w_{n-1})} \frac{C(w_2~w_3~w_4)}{C(w_3~w_4)} \frac{C(w_1~w_2~w_3)}{C(w_2~w_3)} \\ {=} \frac{C(w_{n-2}~w_{n-1}~w_n)}{V} \frac{C(w_{n-3}~w_{n-2}~w_{n-1})}{C(w_{n-2}~w_{n-1})} \frac{C(w_2~w_3~w_4)}{C(w_3~w_4)} \frac{C(w_1~w_2~w_3)}{C(w_2~w_3)} \\ {=} \frac{C(w_1~w_2~w_3)}{V} \frac{C(w_2~w_3~w_4)}{C(w_2~w_3)} \frac{C(w_{n-2}~w_{n-1}~w_n)}{C(w_{n-2}~w_{n-1})} {=} p(w) $ 



## 2 $N$-gram Language Model Implementation

In [31]:
!wget -O train.txt https://raw.githubusercontent.com/qtli/COMP7607-Fall2023/master/assignments/A1/data/lm/train.txt
!wget -O dev.txt https://raw.githubusercontent.com/qtli/COMP7607-Fall2023/master/assignments/A1/data/lm/dev.txt
!wget -O test.txt https://raw.githubusercontent.com/qtli/COMP7607-Fall2023/master/assignments/A1/data/lm/test.txt

SYSTEM_WGETRC = c:/progra~1/wget/etc/wgetrc
syswgetrc = C:\Program Files (x86)\GnuWin32/etc/wgetrc
--2023-10-23 02:55:06--  https://raw.githubusercontent.com/qtli/COMP7607-Fall2023/master/assignments/A1/data/lm/train.txt
���ڽ������� raw.githubusercontent.com... 185.199.109.133, 185.199.108.133, 185.199.111.133, ...
Connecting to raw.githubusercontent.com|185.199.109.133|:443... �����ӡ�
OpenSSL: error:140770FC:SSL routines:SSL23_GET_SERVER_HELLO:unknown protocol
�޷����� SSL ���ӡ�
SYSTEM_WGETRC = c:/progra~1/wget/etc/wgetrc
syswgetrc = C:\Program Files (x86)\GnuWin32/etc/wgetrc
--2023-10-23 02:55:06--  https://raw.githubusercontent.com/qtli/COMP7607-Fall2023/master/assignments/A1/data/lm/dev.txt
���ڽ������� raw.githubusercontent.com... 185.199.109.133, 185.199.108.133, 185.199.111.133, ...
Connecting to raw.githubusercontent.com|185.199.109.133|:443... �����ӡ�
OpenSSL: error:140770FC:SSL routines:SSL23_GET_SERVER_HELLO:unknown protocol
�޷����� SSL ���ӡ�
SYSTEM_WGETRC = c:/progra~1/wget/e

### 2.1 Building vocabulary

**Code**

\# todo



In [32]:
from collections import Counter
import re
import numpy as np
from functools import reduce
from collections import defaultdict

In [33]:
dataset = 'train'

def load_dataset(dataset):
    tokenized_data = []
    tokenized_data_2dim = []
    with open(f'data/lm/{dataset}.txt', encoding='utf-8') as fd:
        lines = fd.readlines()
        for line in lines:
            words = ['<s>'] + re.split(r'\s+', line.strip()) + ['</s>']
            tokenized_data.extend(words)
            tokenized_data_2dim.append(words)
    return tokenized_data, tokenized_data_2dim
        
tokenized_data, tokenized_data_2dim = load_dataset(dataset)

# Step 1: Count token frequencies
token_counts = Counter(tokenized_data)

# Step 2: Replace infrequent tokens with "<UNK>"
min_token_freq = 3
tokenized_data_with_unk = [token if token_counts[token] >= min_token_freq else '<UNK>' for token in tokenized_data]
tokenized_data_with_unk_2dim = [[token if token_counts[token] >= min_token_freq else '<UNK>' for token in line] for line in tokenized_data_2dim]

# Step 3: Add start-of-sentence and end-of-sentence tokens
vocabulary = set(tokenized_data_with_unk)
vocabulary_size = len(vocabulary)

print("Vocabulary size:", vocabulary_size)
# print('<UNK>' in vocabulary)
# print(len(token_counts))

Vocabulary size: 19349


**Discussion**

unigram:

the number of parameters: Vocabulary size 19349

bigram:

the number of parameters: Vocabulary size^2 19349**2

trigram:

the number of parameters: Vocabulary size^3 19349**3



### 2.2 $N$-gram Language Modeling

**Code**

\# todo



In [34]:
"""
load dev set
"""
_, tokenized_data_2dim_dev = load_dataset('dev')
tokenized_data_2dim_dev = [[token if token in vocabulary else '<UNK>' for token in sentence] for sentence in tokenized_data_2dim_dev]

In [35]:
"""
unigram for train set
"""
unigram_counts = Counter(tokenized_data_with_unk)

def calculate_unigram_prob(word):
    return unigram_counts[word] / len(tokenized_data_with_unk)

class Unigram():
    def __init__(self):
        self.prob_list = defaultdict()

    def train(self):
        for sentence in tokenized_data_with_unk_2dim:
            num_words = len(sentence)

            for i in range(num_words):
                word = sentence[i]
                prob = calculate_unigram_prob(word)
                self.prob_list[word] = prob

    def get(self, word):
        return self.prob_list[word]

    def predict(self):
        pass


# Step 4: Calculate perplexity
def calculate_perplexity(data):
    num_words = len(data)
    log_prob_sum = 0

    for i in range(num_words):
        word = data[i]
        prob = calculate_unigram_prob(word)
        log_prob_sum += np.log(prob)

    perplexity = np.exp(log_prob_sum) ** (-1/num_words)
    return perplexity

def report_perplexity(data, dataset, prob_func):
    # Calculate perplexity for each sentence
    sentence_perplexities = []
    for i, sentence in enumerate(data):
        perplexity = prob_func(sentence)
        sentence_perplexities.append(perplexity)


    print(f"Perplexity for each sentence in {dataset} set:")
    for i, perplexity in enumerate(sentence_perplexities):
        print(f"Sentence {i+1}: {perplexity}")
    mean = (np.average(np.array(sentence_perplexities)))
    print(f"average Perplexity in {dataset} set: {mean}")


report_perplexity(tokenized_data_with_unk_2dim, 'train', calculate_perplexity)

Perplexity for each sentence in train set:
Sentence 1: 932.6803488088202
Sentence 2: 1604.4999282473073
Sentence 3: 701.239863746146
Sentence 4: 608.9061296542122
Sentence 5: 568.1406344473174
Sentence 6: 745.9986511040005
Sentence 7: 121.1993007072166
Sentence 8: 1265.847499439491
Sentence 9: 689.3862359290247
Sentence 10: 364.31130087134625
Sentence 11: 881.4849704910911
Sentence 12: 754.9836239403254
Sentence 13: 267.02429790168617
Sentence 14: 630.7825435552716
Sentence 15: 125.30295445183577
Sentence 16: 812.1642908486239
Sentence 17: 595.89369364503
Sentence 18: 298.83844782235343
Sentence 19: 1120.7881888073382
Sentence 20: 1337.4499570827
Sentence 21: 795.1911374990608
Sentence 22: 679.9445302101227
Sentence 23: 814.9274955876401
Sentence 24: 1245.7934687324375
Sentence 25: 900.4361273951015
Sentence 26: 1318.9759002486994
Sentence 27: 1460.6968393055943
Sentence 28: 328.85763924077776
Sentence 29: 796.487258287119
Sentence 30: 413.5935427772011
Sentence 31: 589.5552460647154
S

In [36]:
"""
unigram for dev set
"""
report_perplexity(tokenized_data_2dim_dev, 'dev', calculate_perplexity)

Perplexity for each sentence in dev set:
Sentence 1: 480.6338648731422
Sentence 2: 565.2602023858129
Sentence 3: 572.338655864461
Sentence 4: 651.0178622119655
Sentence 5: 703.5357991382675
Sentence 6: 752.472543665311
Sentence 7: 543.2643167154727
Sentence 8: 1192.3100773097246
Sentence 9: 792.6282570957435
Sentence 10: 1156.11802526704
Sentence 11: 1372.2085098387495
Sentence 12: 1388.2935965911474
Sentence 13: 626.9456972234882
Sentence 14: 695.0393560063995
Sentence 15: 754.4468155737871
Sentence 16: 860.5057085182069
Sentence 17: 1205.7096751289196
Sentence 18: 1194.4072971384355
Sentence 19: 1317.0700213888965
Sentence 20: 978.8117082635681
Sentence 21: 860.5057085182069
Sentence 22: 1148.0359033311195
Sentence 23: 964.2934244949176
Sentence 24: 763.7001119647997
Sentence 25: 865.5987559289224
Sentence 26: 496.5584542753122
Sentence 27: 878.5298228067608
Sentence 28: 730.161146752299
Sentence 29: 600.2972140206895
Sentence 30: 730.161146752299
Sentence 31: 610.4837490342752
Sente

In [37]:
"""
bigram for train
"""
# Step 1: Count bigram frequencies for each sentence
bigram_counts_list = [Counter(zip(sentence, sentence[1:])) for sentence in tokenized_data_with_unk_2dim]
bigram_counts = Counter()
for count in bigram_counts_list:
    bigram_counts.update(count)


def calculate_bigram_prob(word1, word2):
    return bigram_counts[(word1, word2)] / unigram_counts[word1]

# Step 4: Calculate perplexity for each sentence
def calculate_perplexity_bigram(sentence):
    num_words = len(sentence)
    log_prob_sum = 0

    for i in range(1, num_words):
        word1 = sentence[i - 1]
        word2 = sentence[i]
        prob = calculate_bigram_prob(word1, word2)
        log_prob_sum += np.log(prob)

    perplexity = np.exp(log_prob_sum) ** (-1/num_words)
    return perplexity

report_perplexity(tokenized_data_with_unk_2dim, 'train', calculate_perplexity_bigram)


Perplexity for each sentence in train set:
Sentence 1: 70.38911324238197
Sentence 2: 39.325992523441364
Sentence 3: 72.7251235832082
Sentence 4: 74.66132429291169
Sentence 5: 34.68599042866929
Sentence 6: 87.79784531448094
Sentence 7: 13.59278537606081
Sentence 8: 72.10688366089605
Sentence 9: 39.63823811896575
Sentence 10: 98.65703033597347
Sentence 11: 55.78609577066787
Sentence 12: 59.28954884675488
Sentence 13: 32.89651506037297
Sentence 14: 38.68544034051695
Sentence 15: 11.77010901730285
Sentence 16: 50.60975716355662
Sentence 17: 32.6751839142351
Sentence 18: 31.5453570421023
Sentence 19: 31.740403607771885
Sentence 20: 33.93366495224432
Sentence 21: 57.56988419017634
Sentence 22: 103.26125132403047
Sentence 23: 70.62005875089348
Sentence 24: 39.693408396235306
Sentence 25: 46.05935770005363
Sentence 26: 68.94267939166761
Sentence 27: 68.17081615852115
Sentence 28: 46.06798339985692
Sentence 29: 65.76696218770687
Sentence 30: 25.345170009369618
Sentence 31: 29.813095814031925
Se

In [38]:
"""
bigram for dev set
"""
report_perplexity(tokenized_data_2dim_dev, 'dev', calculate_perplexity_bigram)

C:\Users\23139\AppData\Local\Temp\ipykernel_8896\1409823943.py:23: RuntimeWarning: divide by zero encountered in log
  log_prob_sum += np.log(prob)
C:\Users\23139\AppData\Local\Temp\ipykernel_8896\1409823943.py:25: RuntimeWarning: divide by zero encountered in scalar power
  perplexity = np.exp(log_prob_sum) ** (-1/num_words)


Perplexity for each sentence in dev set:
Sentence 1: inf
Sentence 2: 36.468499885422055
Sentence 3: inf
Sentence 4: inf
Sentence 5: inf
Sentence 6: inf
Sentence 7: inf
Sentence 8: inf
Sentence 9: inf
Sentence 10: inf
Sentence 11: inf
Sentence 12: inf
Sentence 13: inf
Sentence 14: inf
Sentence 15: inf
Sentence 16: inf
Sentence 17: inf
Sentence 18: 40.25751272763017
Sentence 19: inf
Sentence 20: inf
Sentence 21: inf
Sentence 22: inf
Sentence 23: inf
Sentence 24: inf
Sentence 25: inf
Sentence 26: inf
Sentence 27: inf
Sentence 28: inf
Sentence 29: inf
Sentence 30: inf
Sentence 31: inf
Sentence 32: inf
Sentence 33: inf
Sentence 34: inf
Sentence 35: inf
Sentence 36: inf
Sentence 37: inf
Sentence 38: inf
Sentence 39: inf
Sentence 40: inf
Sentence 41: inf
Sentence 42: inf
Sentence 43: inf
Sentence 44: inf
Sentence 45: inf
Sentence 46: inf
Sentence 47: inf
Sentence 48: inf
Sentence 49: inf
Sentence 50: inf
Sentence 51: inf
Sentence 52: inf
Sentence 53: inf
Sentence 54: inf
Sentence 55: inf
Sent

**Discussion**

The lower the Perplexity value, the more accurate the model's prediction of the language sequence.

Under the same corpus and model training conditions, the perplexity of the unigram model is higher and the perplexity of the bigram model is lower. Thus, the prediction of the bigram model is more accurate. This is because the bigram model takes into account neighboring The contextual information between words can capture local semantic and syntactic relationships better than the unigram model.

For dev set, the perplexity of the bigram model is inf. This is because the probability of the subsequent words, word1 and word2, is zero, indicating that they were not observed in the training set.


### 2.3 Smoothing

#### 2.3.1 Add-one (Laplace) smoothing

**Code**

\# todo



In [39]:
"""
add-one smoothing for train set
"""
class Bigram():
    def __init__(self, param):
        self.prob_list = defaultdict(lambda: defaultdict(int))
        self.param = param

    def calculate_add_one_smoothed_prob(self, word1, word2):
        numerator = bigram_counts[(word1, word2)] + self.param
        denominator = unigram_counts[word1] + vocabulary_size * self.param
        return numerator / denominator


    def train(self):
        for sentence in tokenized_data_with_unk_2dim:
            num_words = len(sentence)

            for i in range(1, num_words):
                word1 = sentence[i - 1]
                word2 = sentence[i]
                prob = self.calculate_add_one_smoothed_prob(word1, word2)
                self.prob_list[word1][word2] = prob

    def get(self, word1, word2):
        prob = self.prob_list[word1][word2]
        if prob == 0:
            prob = self.param / (unigram_counts[word1] + vocabulary_size * self.param)
        return prob

    def predict(self):
        pass


bigram = Bigram(param=1)
bigram.train()

def report_perplexity_smooth_one(data):
    perplexity_train = []
    for sentence in data:
        num_words = len(sentence)
        log_prob_sum = 0

        for i in range(1, num_words):
            word1 = sentence[i - 1]
            word2 = sentence[i]

            prob = bigram.get(word1, word2)
            log_prob_sum += np.log(prob)

        perplexity = np.exp(log_prob_sum) ** (-1/num_words)
        perplexity_train.append(perplexity)

    print("Perplexity for each sentence:")
    for i, perplexity in enumerate(perplexity_train):
        print(f"Sentence {i+1}: {perplexity}")
    mean = (np.average(np.array(perplexity_train)))
    print(f"average Perplexity: {mean}")
report_perplexity_smooth_one(tokenized_data_with_unk_2dim)

Perplexity for each sentence:
Sentence 1: 1100.7879856408754
Sentence 2: 1123.531771198167
Sentence 3: 971.6682382314165
Sentence 4: 907.4679900432644
Sentence 5: 399.5395533003973
Sentence 6: 1142.9261200224605
Sentence 7: 53.097430730664165
Sentence 8: 1527.987769788966
Sentence 9: 537.0234726776556
Sentence 10: 860.5689482453164
Sentence 11: 893.0472843459099
Sentence 12: 821.9662858063128
Sentence 13: 222.03837395545168
Sentence 14: 490.67809122253095
Sentence 15: 47.187097453953314
Sentence 16: 766.9628499856404
Sentence 17: 373.35018950401656
Sentence 18: 253.7872168707517
Sentence 19: 651.9921897203016
Sentence 20: 885.7226642323557
Sentence 21: 775.6826724062034
Sentence 22: 1346.5923513471562
Sentence 23: 1070.724947081574
Sentence 24: 900.6523184229699
Sentence 25: 797.5650785858339
Sentence 26: 1368.8054628635505
Sentence 27: 1638.8506952795262
Sentence 28: 327.63442400513014
Sentence 29: 1145.7526839647762
Sentence 30: 247.55571078890566
Sentence 31: 350.23392541068506
Sent

In [40]:
"""
add-one smoothing for dev set
"""
report_perplexity_smooth_one(tokenized_data_2dim_dev)

Perplexity for each sentence:
Sentence 1: 496.48796955782745
Sentence 2: 465.11532503937156
Sentence 3: 745.1287033480452
Sentence 4: 737.9857508783093
Sentence 5: 656.2064546310419
Sentence 6: 646.1416695919271
Sentence 7: 342.3161271663158
Sentence 8: 761.543704453692
Sentence 9: 620.5773463319703
Sentence 10: 1164.9724315948017
Sentence 11: 1147.7651349541395
Sentence 12: 1884.0804233565946
Sentence 13: 738.5662440929619
Sentence 14: 742.2382163701851
Sentence 15: 1032.155771724559
Sentence 16: 1137.536202046119
Sentence 17: 737.7077461188153
Sentence 18: 839.9524074687471
Sentence 19: 1560.179386169775
Sentence 20: 1814.1786324742561
Sentence 21: 1137.536202046119
Sentence 22: 1753.5496617937551
Sentence 23: 1129.0502992740526
Sentence 24: 944.8189911082961
Sentence 25: 1124.063061018142
Sentence 26: 457.9326770617148
Sentence 27: 909.132766305782
Sentence 28: 1185.6314015934
Sentence 29: 334.04767974858396
Sentence 30: 1185.6314015934
Sentence 31: 547.4633480250139
Sentence 32: 92

**Discussion**

perplexity increases from 49.9 to 845 for train set. Thus, the accuracy of the bigram decreases.
perplexity decreases from inf to 56.2 for dev set. Thus, the accuracy of the bigram increases.



#### 2.3.2: Add-$k$ smoothing

**Code**

\# todo



In [41]:
"""
add-k smoothing for train set
"""
# Try different values of k
ks = [0.5, 0.05, 0.01]

def get_perplexity_smooth_k(data, model):
    perplexity_train = []
    for sentence in data:
        num_words = len(sentence)
        log_prob_sum = 0

        for i in range(1, num_words):
            word1 = sentence[i - 1]
            word2 = sentence[i]

            prob = model.get(word1, word2)
            log_prob_sum += np.log(prob)

        perplexity = np.exp(log_prob_sum) ** (-1/num_words)
        perplexity_train.append(perplexity)
    return np.average(np.array(perplexity_train))

model_perp = {}
for k in ks:
    bigram = Bigram(param=k)
    bigram.train()
    perp = get_perplexity_smooth_k(tokenized_data_with_unk_2dim, bigram)
    model_perp[perp] = k
print(f"choosig k={model_perp[min(model_perp)]} has the smallest perplexity:{min(model_perp)}")

choosig k=0.01 has the smallest perplexity:95.57466983827976


In [42]:
"""
add-k smoothing for dev set
"""
model_perp = {}
for k in ks:
    bigram = Bigram(param=k)
    bigram.train()
    perp = get_perplexity_smooth_k(tokenized_data_2dim_dev, bigram)
    model_perp[perp] = k
print(f"choosig k={model_perp[min(model_perp)]} has the smallest perplexity:{min(model_perp)}")

choosig k=0.01 has the smallest perplexity:302.40132751838496


**Discussion**

k=0.01 has the smallest perplexity for both train and dev set



#### 2.3.3 Linear Interpolation

In [43]:
"""
build trigram
"""
class Trigram():
    def __init__(self) -> None:
        self.prob_list = defaultdict(lambda: defaultdict(int))

    def calculate_prob(self, word1, word2, word3):
        numerator = self.trigram_counts[(word1, word2, word3)]
        denominator = bigram_counts[(word1, word2)]
        return numerator / denominator


    def train(self):
        # tokenized_data_with_unk_2dim_trigram = [['<s>'] + sentence for sentence in tokenized_data_with_unk_2dim]
        trigram_counts_list = [Counter(zip(sentence, sentence[1:], sentence[2:])) for sentence in tokenized_data_with_unk_2dim]
        self.trigram_counts = Counter()
        for count in trigram_counts_list:
            self.trigram_counts.update(count)

        for sentence in tokenized_data_with_unk_2dim:
            num_words = len(sentence)

            for i in range(2, num_words):
                word1 = sentence[i - 2]
                word2 = sentence[i - 1]
                word3 = sentence[i]
                prob = self.calculate_prob(word1, word2, word3)
                self.prob_list[(word1, word2)][word3] = prob

    def get(self, word1, word2, word3):
        return self.prob_list[(word1, word2)][word3]

In [59]:
unigram = Unigram()
unigram.train()

bigram = Bigram(param=0)
bigram.train()

trigram_model = Trigram()
trigram_model.train()

In [60]:
"""
train hyperparameters for train set
"""
lambda1 = 0.2  # Weight for unigram
lambda2 = 0.4  # Weight for bigram
lambda3 = 0.4  # Weight for trigram

def linear_interpolation_smoothing(word1, word2, word3, lambda1, lambda2, lambda3):
    # Calculate the interpolated probability using weighted averages
    if word1 not in vocabulary: word1 = '<UNK>'
    if word2 not in vocabulary: word2 = '<UNK>'
    if word3 not in vocabulary: word3 = '<UNK>'
    unigram_prob = unigram.get(word3)
    bigram_prob = bigram.get(word2, word3)
    trigram_prob = trigram_model.get(word1, word2, word3)

    interpolated_prob = lambda1 * unigram_prob + lambda2 * bigram_prob + lambda3 * trigram_prob
    return interpolated_prob

# Try different hyperparameter sets
for lambda1 in [0.2, 0.4, 0.6]:
    for lambda2 in [0.2, 0.4, 0.6]:
        for lambda3 in [0.2, 0.4, 0.6]:
            if abs(lambda1 + lambda2 + lambda3 - 1.0) != 0.0:
                continue

            perplexity_train = []
            for sentence in tokenized_data_with_unk_2dim:
                num_words = len(sentence)

                log_prob_sum = 0.0
                for i in range(2, num_words):
                    word1 = sentence[i - 2]
                    word2 = sentence[i - 1]
                    word3 = sentence[i]
                    prob = linear_interpolation_smoothing(word1, word2, word3, lambda1, lambda2, lambda3)

                    log_prob_sum += np.log(prob)

                perplexity = np.exp(log_prob_sum) ** (-1/num_words)
                perplexity_train.append(perplexity)

            mean = (np.average(np.array(perplexity_train)))
            print(f"average Perplexity {lambda1},{lambda2},{lambda3}: {mean}")

average Perplexity 0.2,0.2,0.6: 7.157572271610056
average Perplexity 0.2,0.4,0.4: 8.926377785248244
average Perplexity 0.2,0.6,0.2: 12.57380700755171
average Perplexity 0.4,0.2,0.4: 9.694023344865741
average Perplexity 0.4,0.4,0.2: 13.85291879359984
average Perplexity 0.6,0.2,0.2: 15.65927250916657


In [64]:
"""
train hyperparameters for dev set
"""
# Try different hyperparameter sets
for lambda1 in range(1, 10):
    lambda1 /= 10
    for lambda2 in range(1, 10):
        lambda2 /= 10
        for lambda3 in range(1, 10):
            lambda3 /= 10
            if abs(lambda1 + lambda2 + lambda3 - 1.0) != 0.0:
                continue

            perplexity_train = []
            for sentence in tokenized_data_2dim_dev:
                num_words = len(sentence)

                log_prob_sum = 0.0
                for i in range(2, num_words):
                    word1 = sentence[i - 2]
                    word2 = sentence[i - 1]
                    word3 = sentence[i]
                    prob = linear_interpolation_smoothing(word1, word2, word3, lambda1, lambda2, lambda3)

                    log_prob_sum += np.log(prob)

                perplexity = np.exp(log_prob_sum) ** (-1/num_words)
                perplexity_train.append(perplexity)

            mean = (np.average(np.array(perplexity_train)))
            print(f"average Perplexity {lambda1},{lambda2},{lambda3}: {mean}")

average Perplexity 0.1,0.1,0.8: 274.3352861129805
average Perplexity 0.1,0.2,0.7: 225.2851097126903
average Perplexity 0.1,0.3,0.6: 201.07014564136563
average Perplexity 0.1,0.4,0.5: 186.50786406594918
average Perplexity 0.1,0.5,0.4: 177.19268432997347
average Perplexity 0.1,0.6,0.3: 171.43018519962672
average Perplexity 0.1,0.7,0.2: 168.69161570647185
average Perplexity 0.1,0.8,0.1: 169.5838994511215
average Perplexity 0.2,0.1,0.7: 223.1956780424079
average Perplexity 0.2,0.2,0.6: 187.902655261638
average Perplexity 0.2,0.3,0.5: 170.05364130522338
average Perplexity 0.2,0.4,0.4: 159.45398534676661
average Perplexity 0.2,0.5,0.3: 153.09771596745057
average Perplexity 0.2,0.6,0.2: 150.00828186908404
average Perplexity 0.3,0.1,0.6: 199.69658629273923
average Perplexity 0.3,0.2,0.5: 171.28597318441615
average Perplexity 0.3,0.3,0.4: 156.93375049036405
average Perplexity 0.3,0.4,0.3: 148.8261453778916
average Perplexity 0.3,0.5,0.2: 144.81509927175367
average Perplexity 0.4,0.1,0.5: 187.02

**Code**

\# todo



**Discussion**

for train set
lambda1 = 0.2  # Weight for unigram
lambda2 = 0.2  # Weight for bigram
lambda3 = 0.6  # Weight for trigram
0.2,0.2,0.6 has the smallest perplexity

for dev set
0.3,0.5,0.2 has the smallest perplexity

##### **Optimization**:

\# todo

## 3 Preposition Prediction

In [47]:
!wget -O dev.in https://raw.githubusercontent.com/qtli/COMP7607-Fall2023/master/assignments/A1/data/prep/dev.in
!wget -O dev.out https://github.com/qtli/COMP7607-Fall2023/blob/master/assignments/A1/data/prep/dev.out

SYSTEM_WGETRC = c:/progra~1/wget/etc/wgetrc
syswgetrc = C:\Program Files (x86)\GnuWin32/etc/wgetrc
--2023-10-23 02:56:33--  https://raw.githubusercontent.com/qtli/COMP7607-Fall2023/master/assignments/A1/data/prep/dev.in
���ڽ������� raw.githubusercontent.com... 185.199.109.133, 185.199.108.133, 185.199.111.133, ...
Connecting to raw.githubusercontent.com|185.199.109.133|:443... �����ӡ�
OpenSSL: error:140770FC:SSL routines:SSL23_GET_SERVER_HELLO:unknown protocol
�޷����� SSL ���ӡ�
SYSTEM_WGETRC = c:/progra~1/wget/etc/wgetrc
syswgetrc = C:\Program Files (x86)\GnuWin32/etc/wgetrc
--2023-10-23 02:56:33--  https://github.com/qtli/COMP7607-Fall2023/blob/master/assignments/A1/data/prep/dev.out
���ڽ������� github.com... 20.205.243.166
Connecting to github.com|20.205.243.166|:443... �����ӡ�
OpenSSL: error:1407742E:SSL routines:SSL23_GET_SERVER_HELLO:tlsv1 alert protocol version
�޷����� SSL ���ӡ�


In [85]:
"""
read dev.in & prep by bigram
"""
preposition_list = ['at', 'in', 'of', 'for', 'on']

prep_file = []
with open(f'data/prep/dev.in', encoding='utf-8') as fd:
    with open('data/prep/prep.out', 'w', encoding='utf-8') as file:
        lines = fd.readlines()
        for line in lines:
            words = line.split(' ')
            
            prep_line = []
            for i in range(2, len(words)):
                if (words[i] == '<PREP>'):
                    prob_list = []
                    for preposition in preposition_list:
                        prob = linear_interpolation_smoothing(words[i - 2], words[i - 1], preposition, 0.3,0.5,0.2)
                        prob_list.append(prob)

                    prep = preposition_list[np.argmax(np.array(prob_list))]
                    prep_line.append(prep)
            
            prep_file.append(" ".join(prep_line))

            file.write(" ".join(prep_line) + '\n')

        

In [86]:
"""
calculate the accuracy of the bigram
"""
total = 0
right = 0
with open(f'data/prep/dev.out', encoding='utf-8') as fd_dev:
    with open('data/prep/prep.out', encoding='utf-8') as fd_prep:
        lines_dev = fd_dev.readlines()
        lines_prep = fd_prep.readlines()
        for i in range(len(lines_dev)):
            line_dev = lines_dev[i].strip().split()
            line_prep = lines_prep[i].strip().split()

            for j in range(len(line_dev)):
                right += line_dev[j] == line_prep[j]
            total += len(lines_dev[i])
print(f"accuracy: {right/total * 100}%")

accuracy: 19.106699751861044%


In [84]:
"""
read test.in & predict
"""
preposition_list = ['at', 'in', 'of', 'for', 'on']

prep_file = []
with open(f'data/prep/test.in', encoding='utf-8') as fd:
    with open('data/prep/test.out', 'w', encoding='utf-8') as file:
        lines = fd.readlines()
        for line in lines:
            words = line.split(' ')
            
            prep_line = []
            for i in range(len(words)):
                if (words[i] == '<PREP>'):
                    prob_list = []
                    for preposition in preposition_list:
                        prob = linear_interpolation_smoothing(words[i - 2], words[i - 1], preposition, 0.3,0.5,0.2)
                        prob_list.append(prob)

                    prep = preposition_list[np.argmax(np.array(prob_list))]
                    prep_line.append(prep)
            
            prep_file.append(" ".join(prep_line))

            file.write(" ".join(prep_line) + '\n')